In [19]:
import pandas as pd

In [20]:
# 读取 Excel 文件中的商品销售数据
file_path = 'data/商品销售数据.csv'
try:
    sales_data = pd.read_csv(file_path, encoding='gbk')
    print("数据读取成功，数据基本信息：")
    sales_data.info()
    print("数据前几行信息：")
    print(sales_data.head().to_csv(sep='\t', na_rep='nan'))
except FileNotFoundError:
    print(
        f"未找到文件 {file_path}，请检查文件路径是否正确。")

数据读取成功，数据基本信息：
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8978 entries, 0 to 8977
Data columns (total 11 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   订单号     8978 non-null   object 
 1   设备ID    8978 non-null   object 
 2   应付金额    8978 non-null   float64
 3   实际金额    8978 non-null   float64
 4   商品      8978 non-null   object 
 5   支付时间    8978 non-null   object 
 6   地点      8978 non-null   object 
 7   状态      8978 non-null   object 
 8   提现      8978 non-null   object 
 9   大类      8978 non-null   object 
 10  二级类     8978 non-null   object 
dtypes: float64(2), object(9)
memory usage: 771.7+ KB
数据前几行信息：
	订单号	设备ID	应付金额	实际金额	商品	支付时间	地点	状态	提现	大类	二级类
0	DD201708167493190200943961687	E43A6E078A04228	4.5	4.5	250ml燕塘原味酸奶	2017/6/1 0:01	C	已出货未退款	已提现	饮料	乳制品
1	DD201708167493190206930007675	E43A6E078A04134	2.0	2.0	145ml旺仔牛奶盒装	2017/6/1 0:02	B	已出货未退款	已提现	饮料	乳制品
2	DD201708167493190368633848103	E43A6E078A04172	1.5	1.5	劲仔小鱼（卤香味）	2017/6/1 0:07	A	已出货未

In [21]:
# 按照二级类别分组并对实际金额列求和
category_sales = sales_data.groupby('二级类')['实际金额'].sum().reset_index()
print("各二级类别的销售额：")
print(category_sales)

各二级类别的销售额：
         二级类    实际金额
0        乳制品  5308.5
1         其他     3.2
2       功能饮料  3581.7
3         咖啡   515.0
4       坚果炒货   146.8
5       方便速食  3004.5
6     果冻/龟苓膏    17.0
7       果蔬饮料   891.0
8       植物蛋白  1497.0
9          水  1795.1
10      海味零食   371.8
11      碳酸饮料  2088.4
12    糖果/巧克力   240.7
13        纸巾    84.6
14  肉干/豆制品/蛋  4378.7
15      膨化食品  2799.7
16       茶饮料  4905.0
17     蜜饯/果干   987.9
18      饼干糕点  3837.5


In [22]:
# 对求和结果进行降序排序
category_sales = category_sales.sort_values(by='实际金额', ascending=False)
print("按销售额降序排序后的二级类别销售额：")
print(category_sales)

按销售额降序排序后的二级类别销售额：
         二级类    实际金额
0        乳制品  5308.5
16       茶饮料  4905.0
14  肉干/豆制品/蛋  4378.7
18      饼干糕点  3837.5
2       功能饮料  3581.7
5       方便速食  3004.5
15      膨化食品  2799.7
11      碳酸饮料  2088.4
9          水  1795.1
8       植物蛋白  1497.0
17     蜜饯/果干   987.9
7       果蔬饮料   891.0
3         咖啡   515.0
10      海味零食   371.8
12    糖果/巧克力   240.7
4       坚果炒货   146.8
13        纸巾    84.6
6     果冻/龟苓膏    17.0
1         其他     3.2


In [23]:
# 取排名前 5 的商品类别
top_5_category_sales = category_sales.head(5)
print("排名前 5 的商品类别销售额：")
print(top_5_category_sales)

排名前 5 的商品类别销售额：
         二级类    实际金额
0        乳制品  5308.5
16       茶饮料  4905.0
14  肉干/豆制品/蛋  4378.7
18      饼干糕点  3837.5
2       功能饮料  3581.7


In [24]:
# 统计商品销售数量
product_sales_quantity = sales_data.groupby('商品')['商品'].count().reset_index(name='销售数量')
print("各商品的销售数量：")
print(product_sales_quantity)

各商品的销售数量：
                  商品  销售数量
0         100g*5瓶益力多    26
1     100g卫龙点心面黑椒牛排味     3
2        100g果王咸柑桔罐装    13
3       103g康师傅红烧牛肉面     8
4    107g出前一丁桶面酱香牛肉王     6
..               ...   ...
249            顺宝九制梅     6
250              香脆肠    22
251              香豆干    63
252               鸡爪     7
253               鸭翅   112

[254 rows x 2 columns]


In [25]:
from pyecharts import options as opts
from pyecharts.charts import Funnel

# 提取排名前 5 的商品类别和对应的销售额
categories = top_5_category_sales['二级类'].tolist()
sales = top_5_category_sales[
    '实际金额'].tolist()
# 创建漏斗图对象
funnel = (Funnel().add("商品类别销售额",
                       [list(z) for z in zip(categories, sales)],
                       label_opts=opts.LabelOpts(position="inside")).set_global_opts(
    title_opts=opts.TitleOpts(title="排名前 5 的商品类别销售额漏斗图"),
    toolbox_opts=opts.ToolboxOpts(is_show=True)))
# 渲染图表
funnel.render("./top_5_category_sales_funnel.html")

'/Volumes/Data/04CodeData/gcc-project-py-25-2/商务大数据分析/20250507/top_5_category_sales_funnel.html'

In [26]:
from pyecharts import options as opts
from pyecharts.charts import WordCloud

# 提取商品名称和对应的销售数量
products = product_sales_quantity['商品'].tolist()
quantities = product_sales_quantity[
    '销售数量'].tolist()
# 组合商品名称和销售数量
data = [list(z) for z in zip(products, quantities)]
# 创建词云图对象
wordcloud = (WordCloud().add("",
                             data,
                             word_size_range=[20, 100]).set_global_opts(
    title_opts=opts.TitleOpts(title="商品销售数量词云图"),
    toolbox_opts=opts.ToolboxOpts(is_show=True)))
# 渲染词云图
wordcloud.render("./product_sales_wordcloud.html")

'/Volumes/Data/04CodeData/gcc-project-py-25-2/商务大数据分析/20250507/product_sales_wordcloud.html'